# Extreme Multi-label Machine Model

This Jupyter Notebook goes over various methods of multi-label processing using heathcare data

In [6]:
# Create environemnt if necessary
# conda create -n new environment --file req.txt

UsageError: Line magic function `%conda` not found.


In [2]:
# load data
from zipfile import ZipFile
file_name = "data/data.zip"
# opening the zip file in READ mode
with ZipFile(file_name, 'r') as zip:
    # printing all the contents of the zip file
    zip.printdir()
 
    # extracting all the files
    print('Extracting all the files now...')
    zip.extractall(path='data')
    print('Done!')

File Name                                             Modified             Size
labels_list.hkl                                2018-08-27 10:46:42        75184
X_test.hkl                                     2018-08-27 10:46:30     76046143
X_train.hkl                                    2018-08-27 10:46:30    154382149
y_test.hkl                                     2018-08-27 10:46:34   1139166144
y_train.hkl                                    2018-08-27 10:46:42   2312846144
Extracting all the files now...
Done!


### Baseline Machine Gaussian Naive Bayes Learning Model

In [ ]:
import hickle as hkl
X_train = hkl.load( 'data/X_train.hkl' )
X_test = hkl.load( 'data/X_test.hkl' )
y_test = hkl.load( 'data/y_test.hkl' )
y_train = hkl.load( 'data/y_train.hkl' )

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test = sc.transform(X_test)

In [ ]:
from sklearn.naive_bayes import GaussianNB

classif_list = []
train_score_list, test_score_list = [], []

# Training
print("Training")
for i in range(len(labels_list)):
    y_train_for_this_ub04 = y_train[:,i]
    new_classifier = GaussianNB()
    new_classifier.fit(X_train, y_train_for_this_ub04)
    classif_list.append(new_classifier)

# Test & display results
print("Test and display results")
for i in range(len(labels_list)):
    classif = classif_list[i]
    train_score = float('{0:.3f}'.format(classif.score(X_train, y_train[:,i])))
    test_score = float('{0:.3f}'.format(classif.score(X_test, y_test[:,i])))
    train_score_list.append(train_score)
    test_score_list.append(test_score)
    print('Detecting {} with {}% accuracy (training {}%)'.format(labels_list[i], 100*test_score, 100*train_score))

predict_train = np.zeros_like(y_train)
predict_test = np.zeros_like(y_test)
for i in range(len(labels_list)):
    classif = classif_list[i]
    predict_train[:,i] = classif.predict(X_train)
    predict_test[:,i] = classif.predict(X_test)
acc_train = 1 - np.sum(np.abs(predict_train - y_train))/(y_train.shape[0]*y_train.shape[1])
acc_test = 1 - np.sum(np.abs(predict_test - y_test))/(y_test.shape[0]*y_test.shape[1])
print('###')
print('Global accuracy: testing {}, training {}'.format(acc_test, acc_train))

well_labeled = 0
for i in range(len(y_train)):
    if np.sum(np.abs(y_train[i,:] - predict_train[i,:])) == 0:
        well_labeled +=1
print('Overall {} out of the {} training samples were well labeled'.format(well_labeled,len(y_train)))

well_labeled = 0
for i in range(len(y_test)):
    if np.sum(np.abs(y_test[i,:] - predict_test[i,:])) == 0:
        well_labeled +=1
print('Overall {} out of the {} testing samples were well labeled'.format(well_labeled,len(y_test)))

# Evidemment, en plus d'être mathématiquement désapprouvée, cette méthode est encombrante:
# imaginez avoir à construire un million de classificateurs ! Ce n'est pas du tout extensible à de la classification extrême

### Deep Extreme Multi-label Learning by Zhang et al
Follwing XML methods in the paper [Deep Extreme Multi-label Learning by Zhang et al](https://arxiv.org/pdf/1704.03718.pdf) and [eXtreme Multilabel Classification Notebook](https://github.com/therhappy/xml-tuto/blob/master/eXtreme%20Multilabel%20Classification%20Notebook%20-%20EN.ipynb). 

![Machine Learning Path Image](https://github.com/Smone5/XML_EHR_LABELS/blob/master/images/labelmatrix.png "Machine Learning Path")

The goal in this section is build an embedded vector of the UB-04, ICD-10, CPT and Modifier labels. This embedded vector will be used to predict the correct label for EHR procedures.


#### Build Labels Embedded Graph
1. Load data
2. Build edges list
3. Convert Label Edges to Embedded Vectors
4. Convert Features to Embedded Vectors

##### 1. Load data

In [1]:
import numpy as np
import hickle as hkl

In [2]:
y_train = hkl.load( 'data/y_train.hkl' )
labels_list = hkl.load('data/labels_list.hkl' )

In [3]:
# view imported lables
labels_list[0:5]

['10022', '10060', '10120', '10160', '10180']

In [4]:
# view imported trianing labels
y_train[0:5]

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

In [5]:
print("Count of label names: ", len(labels_list))

Count of label names:  8630


In [6]:
#y_train = y_train[0:1000]
print("Labels training rows", y_train.shape[0])
print("Labels training columns", y_train.shape[1])

Labels training rows 67000
Labels training columns 8630


Note:
The label columns and training columns must be the same size to continue.

##### 2. Build edges list

In [7]:
edges = [] # blank list to hold edges
matrix = np.zeros((y_train.shape[0],y_train.shape[1])) #blank matrix to hold weights
print("Matrix rows", matrix.shape[0])
print("Matrix columns", matrix.shape[1])

Matrix rows 67000
Matrix columns 8630


In [8]:
%%time
for row in y_train:
    act = list(np.where(row == 1))
    act = [list(i) for i in act ][0]
    for i in range(len(act)):
        for j in range(len(act)):
            matrix[i,act[j]] +=1
            if i < j:
                edges.append([act[i],act[j]])
        

Wall time: 17.6 s


In [9]:
# Remove duplicate edges from list
edges2 = [[x,y] for x,y in (set(tuple(x) for x in edges))]

In [10]:
#View first 5 rows of edges
edges2[:5]

[[292, 8167], [2538, 2974], [959, 3912], [1559, 1957], [3897, 4036]]

In [22]:
print(len(edges2))

330383


In [11]:
# View the output of the weight matrix from loop
print(matrix)

[[  1.  10.   1. ... 267. 613.  47.]
 [  1.  10.   1. ... 267. 613.  47.]
 [  1.  10.   1. ... 267. 613.  47.]
 ...
 [  0.   0.   0. ...   0.   0.   0.]
 [  0.   0.   0. ...   0.   0.   0.]
 [  0.   0.   0. ...   0.   0.   0.]]


In [23]:
print(len(matrix))

67000


In [12]:
# Normalize the matrix by columns
from sklearn.preprocessing import normalize
norm_matrix = normalize(matrix, axis=1, norm='l1')

In [24]:
print(len(norm_matrix))

67000


In [13]:
'''
# code for converting the numerical number back to original label for checking.
label_dict = {}
for i in range(len(labels_list)):
    label_dict[i] = labels_list[i]

for i in range(len(edges2)):
    val1 = edges2[i][0]
    val2 = edges2[i][1]
    edges2[i][0] = label_dict[val1]
    edges2[i][1] = label_dict[val2]
'''

'\n# code for converting the numerical number back to original label for checking.\nlabel_dict = {}\nfor i in range(len(labels_list)):\n    label_dict[i] = labels_list[i]\n\nfor i in range(len(edges2)):\n    val1 = edges2[i][0]\n    val2 = edges2[i][1]\n    edges2[i][0] = label_dict[val1]\n    edges2[i][1] = label_dict[val2]\n'

In [14]:
import networkx as nx
G=nx.Graph()
for edge in edges2:
        G.add_edge(edge[0], edge[1])

In [15]:
# save as edge list file
with open('node2vec/graph/labels.edgelist', 'w') as f:
    for edge in G.edges():
        f.write("{} {}\n".format(edge[0] ,edge[1]))

##### Analyze the graph in GraphCrunch 2 or Gephi
At this point you could visulize the graph in GraphCrunch 2 or Gephi
+ [GraphCrunch 2](http://www0.cs.ucl.ac.uk/staff/natasa/graphcrunch2/index.html)
+ [Paper](https://bmcbioinformatics.biomedcentral.com/articles/10.1186/1471-2105-12-24)

##### 3. Convert Label Edges to Embedded Vectors
There are four methods to convert a network graph each node into a network as a low-dimensional feature vector.

1. [Deepwalk](https://github.com/phanein/deepwalk)
2. [Node2Vec](https://snap.stanford.edu/node2vec/)
3. [Struct2Vec](https://github.com/leoribeiro/struc2vec)
4. Graphlets

Due a paper from Shawn Gu and Tijana Milenković called [*Graphlets versus node2vec and struc2vec in the task of network alignment*](https://www.groundai.com/project/graphlets-versus-node2vec-and-struc2vec-in-the-task-of-network-alignment/), in certain situations a graphlet could outperform Node2Vec or Struct2Vec to quantify node similarities.

In this section two embedded graphs will be made. One, using Node2Vec and the second using Graphlets. 

*Note* :To use Node2Vec, you must use a Python 2.7 environment at the time of writing this

###### Node2Vec
To run Node2Vec, you first must download the repository and run the line below while in folder the *node2vec*

*python src/main.py --input graph/labels.edgelist --output emb/labels.txt*

###### Graphlets
TBD

In [16]:
import gensim
gmodel=gensim.models.KeyedVectors.load_word2vec_format('node2vec/emb/test.txt')

C:\Users\amelton005\AppData\Local\Continuum\anaconda3\envs\Standard Analytics\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [20]:
y_train_embed = gmodel[gmodel.vocab]

In [47]:
# Plot Word Vectors Using PCA

from sklearn.decomposition import PCA
from matplotlib import pyplot as plt

pca = PCA(n_components=2)
result = pca.fit_transform(y_train_embed)
# create a scatter plot of the projection
plt.figure(figsize=(150,150))
plt.scatter(result[:, 0], result[:, 1])
words = list(gmodel.wv.vocab)
for i, word in enumerate(words):
	plt.annotate(word, xy=(result[i, 0], result[i, 1]))
plt.savefig("images/PCA_graph.png")
plt.show()

C:\Users\amelton005\AppData\Local\Continuum\anaconda3\envs\Standard Analytics\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  # This is added back by InteractiveShellApp.init_path()


In [46]:
result = gmodel.most_similar(positive=['778', '355'])
result

[('350', 0.9403359293937683),
 ('3233', 0.9307347536087036),
 ('8593', 0.9290716648101807),
 ('3224', 0.9268524646759033),
 ('2482', 0.9265989065170288),
 ('1005', 0.9253909587860107),
 ('6839', 0.9252694845199585),
 ('7370', 0.9250996112823486),
 ('7098', 0.924761176109314),
 ('7540', 0.9246740341186523)]

In [21]:
print("Rows: ", y_train_embed.shape[0])
print("Columns: ",y_train_embed.shape[1])

Rows:  8017
Columns:  128


##### 4. Convert Features to Embedded Vectors

In [25]:
X_train = hkl.load( 'data/X_train.hkl' )
X_test = hkl.load( 'data/X_test.hkl' )

y_train = hkl.load( 'data/y_train.hkl' )
y_test = hkl.load( 'data/y_test.hkl' )

In [26]:
print("X_train Rows:", X_train.shape[0])
print("X_train Columns:", X_train.shape[1])

X_train Rows: 67000
X_train Columns: 287


In [150]:
print("y_train Rows:", y_train.shape[0])
print("y_train Columns:", y_train.shape[1])

y_train Rows: 67000
y_train Columns: 8630


In [116]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test = sc.transform(X_test)

In [ ]:
# Project label matrix y_train t 

In [162]:
norm_matrix[0].shape[0]

8630

In [58]:
def compile_model(model, k):
    
    from keras.optimizers import RMSprop, SGD
    import tensorflow as tf
    from keras import backend as K

    def auc(y_true, y_pred):
        auc = tf.metrics.auc(y_true, y_pred)[1]
        K.get_session().run(tf.local_variables_initializer())
        return auc  
    
    def as_keras_metric(method):
        import functools
        from keras import backend as K
        import tensorflow as tf
        @functools.wraps(method)
        def wrapper(self, args, **kwargs):
            """ Wrapper for turning tensorflow metrics into keras metrics """
            value, update_op = method(self, args, **kwargs)
            K.get_session().run(tf.local_variables_initializer())
            with tf.control_dependencies([update_op]):
                value = tf.identity(value)
            return value
        return wrapper
    
    @as_keras_metric
    def precision_at_thresholds(y_true, y_pred, thresholds=[0.25, 0.50]):
        return tf.metrics.precision_at_thresholds(y_true, y_pred, thresholds)
    
    @as_keras_metric
    def p_at_k1(y_true, y_pred, k=1):
        return tf.metrics.precision_at_k(tf.cast(y_true, tf.int64), y_pred, k)

    @as_keras_metric
    def p_at_k2(y_true, y_pred, k=2):
        return tf.metrics.precision_at_k(tf.cast(y_true, tf.int64), y_pred, k)
    
    @as_keras_metric
    def p_at_k3(y_true, y_pred, k=3):
        return tf.metrics.precision_at_k(tf.cast(y_true, tf.int64), y_pred, k)
    
    @as_keras_metric
    def p_at_k4(y_true, y_pred, k=4):
        return tf.metrics.precision_at_k(tf.cast(y_true, tf.int64), y_pred, k)
    
    @as_keras_metric
    def p_at_k5(y_true, y_pred, k=5):
        return tf.metrics.precision_at_k(tf.cast(y_true, tf.int64), y_pred, k)
    
    model.compile(  loss='binary_crossentropy',
                    optimizer=SGD(lr=0.015, momentum=0.9, decay=0.0005),
                    metrics=[p_at_k1, p_at_k5])
    return model

In [158]:
y_conti = np.dot(y_train, y_train_embed)

ValueError: shapes (67000,8630) and (8017,128) not aligned: 8630 (dim 1) != 8017 (dim 0)

In [156]:
from keras.layers.normalization import BatchNormalization

# create model
from keras.layers import Input, Dense, Dropout
feat_input = Input(shape=(287,), dtype='float32_ref')
x = Dense(287, activation='relu')(feat_input)
x = Dense(287, activation='relu')(x)
x = Dropout(0.25)(x)
x = BatchNormalization()(x)


preds = Dense(128, activation='sigmoid')(x)

from keras.models import Model
model = Model(inputs=feat_input, outputs=preds)
model = compile_model(model, k=2)

In [157]:
hist = model.fit(X_train, y_train_embed, validation_split=0.1, epochs=1, batch_size=256, shuffle=True, class_weight='auto')

ValueError: Input arrays should have the same number of samples as target arrays. Found 67000 input samples and 8017 target samples.

In [148]:
from sklearn.ensemble import RandomForestRegressor
regressor = RandomForestRegressor(n_estimators=100, n_jobs=-1)
regressor.fit(X_train, y_train)


KeyboardInterrupt: 

In [ ]:
from sklearn.cluster import KMeans
from sklearn import metrics

NUM_CLUSTERS=20

kmeans = KMeans(n_clusters=NUM_CLUSTERS)
kmeans.fit(X)

In [ ]:
metrics.accuracy(X, y_pred_kmeans)

In [ ]:
labels = kmeans.labels_
centroids = kmeans.cluster_centers_

In [ ]:
print ("Cluster id labels for inputted data")
print (labels)
print ("Centroids data")
print (centroids)
 
print ("Score (Opposite of the value of X on the K-means objective which is Sum of distances of samples to their closest cluster center):")
print (kmeans.score(X))
 
silhouette_score = metrics.silhouette_score(X, labels, metric='euclidean')
 
print ("Silhouette_score: ")
print (silhouette_score)

##### 4. Build X path for features

In [ ]:
# import data
X_train = hkl.load( 'data/X_train.hkl' )
X_test = hkl.load( 'data/X_test.hkl' )